# Housing Dataset

- Ecaluation metric RMSE (root-mean-sqred-error)

Best approach is to go throug _every_ feature. However, only few features will be analyzed here.  

Subject matter knowladge is rquired: what each feature means, implies. 

If there is not much data __outside data__ can be used.  

Some data is categorical. (Some data is numerical, while it is actually categorical).  

Using ChatGPT:  
Pass the data names, descriptions, ask to keep in memory.  

Important: set a task list for the project:
- Cleaning/feature feature exploration,
- EDA...
- ...
- Feature engeneering
- Ensembling



In [4]:
# Import relevant packages (in the beginning)
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
import scipy.stats as stats
from IPython.display import display, HTML

# Basic Data Exploration
1. Import the data 
2. Look at summary statistics
3. Evaluate Null Vals

__NOTE__ chatGPT can be used to get functions to e.g., get a scrollable look at the table

In [8]:
df = pd.read_csv("./train.csv")

In [9]:
def display_scrollable(df, height=300):
    """
    Display a scrollable view of a DataFrame in a Jupyter Notebook.
    
    Parameters:
    - df: The pandas DataFrame you want to display.
    - height: The height of the scrollable view in pixels. Default is 300px.
    """
    # Convert DataFrame to HTML
    df_html = df.to_html().replace("<table", f"<table style='height: {height}px; display: block; overflow-y: scroll;'")
    
    # Display the scrollable table
    display(HTML(df_html))
display_scrollable(df)

In [10]:
# Describe numerical features (Recall that some features are 
# categorical, but saved as numbers)
numerical_features = df.select_dtypes(include=[np.number])
numerical_features.describe()

Id   MSSubClass  LotFrontage        LotArea  OverallQual  \
count  1460.000000  1460.000000  1201.000000    1460.000000  1460.000000   
mean    730.500000    56.897260    70.049958   10516.828082     6.099315   
std     421.610009    42.300571    24.284752    9981.264932     1.382997   
min       1.000000    20.000000    21.000000    1300.000000     1.000000   
25%     365.750000    20.000000    59.000000    7553.500000     5.000000   
50%     730.500000    50.000000    69.000000    9478.500000     6.000000   
75%    1095.250000    70.000000    80.000000   11601.500000     7.000000   
max    1460.000000   190.000000   313.000000  215245.000000    10.000000   

       OverallCond    YearBuilt  YearRemodAdd   MasVnrArea   BsmtFinSF1  ...  \
count  1460.000000  1460.000000   1460.000000  1452.000000  1460.000000  ...   
mean      5.575342  1971.267808   1984.865753   103.685262   443.639726  ...   
std       1.112799    30.202904     20.645407   181.066207   456.098091  ...   
min       1.000000  1872.000000   1950.000000     0.000000     0.000000  ...   
25%       5.000000  1954.000000   1967.000000     0.000000     0.000000  ...   
50%       5.000000  1973.000000   1994.000000     0.000000   383.500000  ...   
75%       6.000000  2000.000000   2004.000000   166.000000   712.250000  ...   
max       9.000000  2010.000000   2010.000000  1600.000000  5644.000000  ...   

        WoodDeckSF  OpenPorchSF  EnclosedPorch    3SsnPorch  ScreenPorch  \
count  1460.000000  1460.000000    1460.000000  1460.000000  1460.000000   
mean     94.244521    46.660274      21.954110     3.409589    15.060959   
std     125.338794    66.256028      61.119149    29.317331    55.757415   
min       0.000000     0.000000       0.000000     0.000000     0.000000   
25%       0.000000     0.000000       0.000000     0.000000     0.000000   
50%       0.000000    25.000000       0.000000     0.000000     0.000000   
75%     168.000000    68.000000       0.000000     0.000000     0.000000   
max     857.000000   547.000000     552.000000   508.000000   480.000000   

          PoolArea       MiscVal       MoSold       YrSold      SalePrice  
count  1460.000000   1460.000000  1460.000000  1460.000000    1460.000000  
mean      2.758904     43.489041     6.321918  2007.815753  180921.195890  
std      40.177307    496.123024     2.703626     1.328095   79442.502883  
min       0.000000      0.000000     1.000000  2006.000000   34900.000000  
25%       0.000000      0.000000     5.000000  2007.000000  129975.000000  
50%       0.000000      0.000000     6.000000  2008.000000  163000.000000  
75%       0.000000      0.000000     8.000000  2009.000000  214000.000000  
max     738.000000  15500.000000    12.000000  2010.000000  755000.000000  

[8 rows x 38 columns]

In [11]:
# Summary statistics for numerical feature
summary_stats = numerical_features.describe().T # invert table
display_scrollable(summary_stats)

In [12]:
print(f"Data has {df.shape} features")

Data has (1460, 81) features


__NOTE__:
Notice that some data like year should not be continous.  
Also some years, like 2008, had a housing bubble burst and inference on this year might be different.  
__Conclusion__: some features should be moved from continous to categorical and vice versa  
__KEY__: use industry and external information to change/augment the dataset

In [14]:
# Consider categorical data
categorical_features = df.select_dtypes(include=[object])
cat_sum = categorical_features.describe().T
display_scrollable(cat_sum)

__NOTE__ some features are categorical even if in the dataset they are given as numerical

In [16]:
# Exploring the null values
missing = (df.isnull().sum() / len(df)) * 100
display_scrollable(missing.to_frame())

__NOTE__ some features have A LOT of missing values $>90\%$. One can 
- Remove them
- Get data from outside
- Make it categorical with one-hot encoding (1 for there is data, $0$ if there is not)

In [17]:
# Exploring rows with missing values 
rows_with_missing = df[df.isnull().any(axis=1)]
display_scrollable(rows_with_missing)

In [18]:
df.columns # print all the features

Index(['Id', 'MSSubClass', 'MSZoning', 'LotFrontage', 'LotArea', 'Street',
       'Alley', 'LotShape', 'LandContour', 'Utilities', 'LotConfig',
       'LandSlope', 'Neighborhood', 'Condition1', 'Condition2', 'BldgType',
       'HouseStyle', 'OverallQual', 'OverallCond', 'YearBuilt', 'YearRemodAdd',
       'RoofStyle', 'RoofMatl', 'Exterior1st', 'Exterior2nd', 'MasVnrType',
       'MasVnrArea', 'ExterQual', 'ExterCond', 'Foundation', 'BsmtQual',
       'BsmtCond', 'BsmtExposure', 'BsmtFinType1', 'BsmtFinSF1',
       'BsmtFinType2', 'BsmtFinSF2', 'BsmtUnfSF', 'TotalBsmtSF', 'Heating',
       'HeatingQC', 'CentralAir', 'Electrical', '1stFlrSF', '2ndFlrSF',
       'LowQualFinSF', 'GrLivArea', 'BsmtFullBath', 'BsmtHalfBath', 'FullBath',
       'HalfBath', 'BedroomAbvGr', 'KitchenAbvGr', 'KitchenQual',
       'TotRmsAbvGrd', 'Functional', 'Fireplaces', 'FireplaceQu', 'GarageType',
       'GarageYrBlt', 'GarageFinish', 'GarageCars', 'GarageArea', 'GarageQual',
       'GarageCond', 'PavedDrive

## Explore the dependent variable 
- Should the data be normalized
- Is there a skew in data

In [28]:
import scipy.stats as stats

# Fit a normal distribution to the SalePrice Data
mu, sigma = stats.norm.fit(df["SalePrice"])

# create histogram of the column
hist_data = go.Histogram(x=df['SalePrice'],  nbinsx=50, 
                         name="Histogram", opacity =.75, 
                         histnorm="probability density")

# Calculate the notmal distribution based on the fitted parameters
x_norm = np.linspace(df["SalePrice"].min(), 
                     df["SalePrice"].max(), 100)
y_norm = stats.norm.pdf(x_norm, mu, sigma)

# Create a normal distribution overaly
norm_data = go.Scatter(x=x_norm, y=y_norm, mode="lines", 
                       name=f"Normal dist (mu={mu:.2f}, sigm={sigma:.2f}")

# combine the histogram an overlay
fig = go.Figure(data=[hist_data, norm_data])

# Set layout and plot
fig.update_layout(
    title="SalePrice Distribution", 
    xaxis_title="SalePrice",
    yaxis_title="Density",
)

# Create a Q-Q plot
qq_data = stats.probplot(df["SalePrice"],dist="norm")
qq_fig = px.scatter(x=qq_data[0][0], y=qq_data[0][1], 
                    labels={"x":"Theoretical Quantities",
                            "y":"Ordered Values"})
qq_fig.update_layout(
    title="Q-Q plot"
)

# Calculate the line of best fit
slope, intercept, r_value, p_value, std_err = \
    stats.linregress(qq_data[0][0], qq_data[0][1])
line_x = np.array(qq_data[0][0])
line_y = intercept + slope * line_x

# add the line of the best fit to Q-Q plot
line_data = go.Scatter(x=line_x, y=line_y, mode="lines", name="Normal line")

# Update Q-Q plot with normal line
qq_fig.add_trace(line_data)

# Show the plots
fig.show()
qq_fig.show()

__Note__:  
The first plot shows that the data deviates from normal distribution extracted from data (fitting the gaussian to data)

The quantile-quantile, the probability plot, comaprres two probability distributions by showing their _quantiles_ against each other. This is a parametric curve where the parameter is the __index__ of the quantile interval. 
- For _similar_ distributions, the points in Q-Q plot will lie on the identiy $y=x$ line. 
- For distributions are _linearly related_ than there would be a stright line, but different from $y=x$.  

The Q-Q plot (also called 'probability plot') can be considered as a non-parametric approach to comapre underlying distributions. It is well suited to comapre theoretical with experimental data. It provides assessment of the goodness of the fit that is _graphical_. 

So the plot shows that the distribution in data is non-learly related to gaussian. So perphas a $\log()$ transform would be required

Source: (source)[https://en.wikipedia.org/wiki/Q%E2%80%93Q_plot]

## What questions do we want to ask from data?

Key qantity of interest: _Price_

1. Dists. of welling types and their relations to sale price
2. Does zoning impact sale price
3. Does street and alley access affect the sale price
4. What is the average sale price by the property shape
5. Is there a correlation between property adge and sale price?

> _New approach_: Feed the data features to ChatGPT and ask _What questions_ would we be interesting?

In [37]:
# Distribution of welling types and their relation to sale prices
dwelling_types = df['BldgType'].value_counts()
dwelling_prices = df.groupby("BldgType")['SalePrice'].mean()

fig1 = go.Figure(data=[go.Bar(x=dwelling_types.index,
                              y=dwelling_types.values,
                              text=dwelling_types.values,
                              textposition="outside",
                              width=0.4)
                              ])
fig1.update_layout(
    title="Distribution of Building Types",
    xaxis_title="Building Type",
    yaxis_title="Count"
)

formatted_dwelling_prices = ["$"+f"{val:,.2f}" for val in dwelling_prices.values]
fig2 = go.Figure(data=[go.Bar(x=dwelling_prices.index,
                              y=dwelling_prices.values,
                              text=formatted_dwelling_prices,
                              textposition="outside",
                              width=0.4)])

fig2.update_layout(
    title="Average Sale Price by Building Type",
    xaxis_title="Building price",
    yaxis_title="Count"
)

fig1.show()
fig2.show()

__Note__:  
Analysis shows that most common type of dwellings is _1Fam_, while high sale prices are high for bith _1Fam_ and _TwinhsE_. 

In [44]:
# Zoning impact on sale prices 
zoning_prices = df.groupby("MSZoning")["SalePrice"].mean()
fig3 = px.bar(x=zoning_prices.index, y=zoning_prices.values, text=zoning_prices.values)
fig3.update_traces(texttemplate="$%{text:,.0f}", textposition="outside")
fig3.update_yaxes(title="Sale Price",tickprefix="$",tickformat=",")
fig3.update_xaxes(title="Zoning")
fig3.update_layout(uniformtext_minsize=8,uniformtext_mode="hide")
fig3.show()

__NOTE__:  
C - commertial 
FV - floating village 
RH - residential high density 

_NOTE_ some data did not have enough values

In [46]:
zoning_prices = df.groupby("Street")["SalePrice"].mean()
fig3 = px.bar(x=zoning_prices.index, y=zoning_prices.values, 
              text=zoning_prices.values,title="Aver.Sale.Price.By.Street.Type")
fig3.update_traces(texttemplate="$%{text:,.0f}", textposition="outside")
fig3.update_yaxes(title="Sale Price",tickprefix="$",tickformat=",")
fig3.update_xaxes(title="Zoning")
fig3.update_layout(uniformtext_minsize=8,uniformtext_mode="hide")
fig3.show()

zoning_prices = df.groupby("Alley")["SalePrice"].mean()
fig3 = px.bar(x=zoning_prices.index, y=zoning_prices.values, 
              text=zoning_prices.values,title="Aver.Sale.Price.By.Alley.Type")
fig3.update_traces(texttemplate="$%{text:,.0f}", textposition="outside")
fig3.update_yaxes(title="Sale Price",tickprefix="$",tickformat=",")
fig3.update_xaxes(title="Zoning")
fig3.update_layout(uniformtext_minsize=8,uniformtext_mode="hide")
fig3.show()

In [48]:
# reating new feature 
df["PropertyAge"] = df["YrSold"] - df["YearBuilt"]

# Calculate correlation between property Age and Sale Prices
age_price_corr = df["PropertyAge"].corr(df["SalePrice"])
print(f"Correlation between the age and price: {age_price_corr}")

# Scatter plot
fig9 = px.scatter(df,x="PropertyAge",y="SalePrice",title="Age Vs Price",
                  color='PropertyAge')
fig9.update_layout()
fig9.show()

Correlation between the age and price: -0.5233504175468159


__NOTE__ W eobserver a geneal _downward_ trend with correlation coeffieicne $-0.5$.  


In [51]:
# Consider correlation between Livin Area and Sale Price
living_area_prices_corr = df["GrLivArea"].corr(df["SalePrice"])
print(f"Correlation between living area and Sale Price = {living_area_prices_corr}")

# Create a scatter plot 
fig10 = px.scatter(df, x='GrLivArea', y='SalePrice', 
                   title='Living Area (above grade) vs Sale Price',color='GrLivArea')
fig10.update_layout()

fig10.show()

Correlation between living area and Sale Price = 0.7086244776126522


__NOTE__: We observe strong correlation between living area and price (as expected)

In [59]:
# Make a Box Plot of Price over the Years
yearly_avg_sale_price = df.groupby('YrSold')['SalePrice'].mean()

fig13 = px.box(df, x='YrSold', y='SalePrice', title='Sale Price Trends Over the Years',
               points=False)

fig13.add_trace(px.line(x=yearly_avg_sale_price.index, 
                        y=yearly_avg_sale_price.values).data[0])

fig13.update_traces(line=dict(color='purple', width=4), 
                    selector=dict(type='scatter', mode='lines'))

for year, avg_price in yearly_avg_sale_price.items():
    fig13.add_annotation(
        x=year,
        y=avg_price,
        text=f"{avg_price:,.0f}",
    )

fig13.update_layout()

fig13.show()

__NOTE__: Large variation in 2007 indicate the housing market burst

# Creating Data Processing Pipeline

Pipelines allow you to chain actions
- This is clean way to chain functions together
- Create a Data cleaning pipeline

Usefull to have the same procedure for _train_ and _test_ data (preprocessed in the same way)


In [61]:
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler, OneHotEncoder

# Create transformers for numerical and categorical columns
numerical_transformer = Pipeline(steps=[
    ('imputer', SimpleImputer(strategy="mean")),
    ('scaler', StandardScaler())
])

categorical_transformer = Pipeline(steps=[
    ("imputer", SimpleImputer(strategy="constant", # (if it is Null -> new category)
                              fill_value="missing")),
    ("onehot", OneHotEncoder(handle_unknown="ignore", # Adding columns for 'hot' and 'cold', 
                             sparse=False))
])

In [62]:
# Update categorical and numerical columns
categorical_columns = df.select_dtypes(include=["object","category"]).columns
numerical_columns = df.select_dtypes(include=["int64","float64"]).columns

# remove target variable from numerical columns
numerical_columns = numerical_columns.drop("SalePrice")

# Combine transpferms using ColumnTransformer
preprocessor = ColumnTransformer(
    transformers=[
        ("num", numerical_transformer, numerical_columns),
        ("cat", categorical_transformer, categorical_columns)
    ], remainder="passthrough"
)

# Create a pipeline with the preprocessor 
pipeline = Pipeline(steps=[
    ("preprocessor", preprocessor)
])

# Apply the pipeline to the dataset 
X = df.drop("SalePrice", axis = 1)
y = np.log(df["SalePrice"]) # INCLUDE NORMALIZATION

# Clean the data using the pipeline outlined above
X_preprocessed = pipeline.fit_transform(X)

# Fit Parameter Tune Models

In [66]:
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
from sklearn.model_selection import GridSearchCV, KFold, cross_val_score

# Split the data into train. test.csv
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test \
    = train_test_split(X_preprocessed, y, test_size=0.2, random_state=42)

# This code was generated by ChatGPT primarely

# Define the models
models = {
    "LinearRegression" : LinearRegression(),
    "RandomForest": RandomForestRegressor(random_state=42),
    "XGBoost": XGBRegressor(random_state=42)
}

# Define hyperparameter grids for each model
param_grids = {
    "LinearRegression":{},
    "RandomForest":{
        "n_estimators":[100,200,500],
        "max_depth":[None,10,30],
        "min_samples_split":[2,5,10]
    },
    "XGBoost":{
        "n_estimators":[100,200,500],
        "learning_rate":[.01, .1, .3],
        "max_depth":[3,6,10]
    }
}

# 
cv = KFold(n_splits=3,shuffle=True,random_state=42)

# Train the models
grids = {}
for model_name, model in models.items():
    grids[model_name] = GridSearchCV(estimator=model, 
                                     param_grid=param_grids[model_name],
                                     cv=cv, 
                                     scoring="neg_mean_squared_error",
                                     n_jobs=-1,
                                     verbose=2)
    grids[model_name].fit(X_train, y_train)
    best_params = grids[model_name].best_params_
    best_score = np.sqrt(-1 * grids[model_name].best_score_)

    print(f"Best params for {model_name} are {best_params}")
    print(f"Best RMSE for {model_name} is {best_score}\n")



Fitting 3 folds for each of 1 candidates, totalling 3 fits
[CV] END .................................................... total time=   0.0s
[CV] END .................................................... total time=   0.0s
[CV] END .................................................... total time=   0.1s
Best params for LinearRegression are {}
Best RMSE for LinearRegression is 28693988822.52583

Fitting 3 folds for each of 27 candidates, totalling 81 fits
[CV] END max_depth=None, min_samples_split=5, n_estimators=100; total time=   2.3s
[CV] END max_depth=None, min_samples_split=5, n_estimators=100; total time=   2.5s
[CV] END max_depth=None, min_samples_split=5, n_estimators=100; total time=   2.6s
[CV] END max_depth=None, min_samples_split=2, n_estimators=100; total time=   3.0s
[CV] END max_depth=None, min_samples_split=2, n_estimators=100; total time=   3.1s
[CV] END max_depth=None, min_samples_split=2, n_estimators=100; total time=   3.1s
[CV] END max_depth=None, min_samples_split=10,

__Note__:  
Linear regression results are _VERY_ bad. Reson: 
- Large amount of data
- Correlation between variables

In [69]:
# Simple ML model (CPU only)
from sklearn.neural_network import MLPRegressor


# Here data HAS TO BE scaled (as it was already done so, just copy)
X_train_scaled = X_train.copy()
X_test_scaled = X_test.copy()

# Create a MLPRegressor instance
mlp = MLPRegressor(random_state=42,max_iter=10000,
                   n_iter_no_change=3, # early stopping parameter
                   learning_rate_init=.001)

# Define Parameter grid tuning
param_grid = {
    "hidden_layer_sizes":[(10,),(10,10),(10,10,10),(25)], # architectures
    "activation":["relu","tanh"],
    "solver":["adam"],
    "alpha":[.0001,.001,.01], # normalization parameter
    "learning_rate":["constant","invscaling","adaptive"]
}

# Create a grid search object
grid_search_mlp = GridSearchCV(mlp,param_grid,
                               scoring="neg_mean_squared_error",
                               cv=3,
                               n_jobs=-1,
                               verbose=1)

# Fit model on the trainin data
grid_search_mlp.fit(X_train_scaled, y_train)

# Print best parameters
print("best params found:", grid_search_mlp.best_params_)

# evaluate the model on the test data
best_score = np.sqrt(-1 * grid_search_mlp.best_score_)
print("Test score: ", best_score)

Fitting 3 folds for each of 72 candidates, totalling 216 fits
best params found: {'activation': 'relu', 'alpha': 0.0001, 'hidden_layer_sizes': (10, 10), 'learning_rate': 'constant', 'solver': 'adam'}
Test score:  0.23248885526714724


# Principle Component analysis 
- Adressing strong correlation between predictors

Analysis gives the new nmber of not-correlated features

In [71]:
from sklearn.decomposition import PCA

pca = PCA()

X_pca_pre = pca.fit_transform(X_preprocessed)

# calculate the cumulative explained variance
cum_ep_car = np.cumsum(pca.explained_variance_ratio_)

# chose the number of components based on the explained variance threshold
n_components = np.argmax(cum_ep_car >= .95) + 1

pca = PCA(n_components=n_components)

pipeline_pca = Pipeline(steps=[
    ("preprocessor",preprocessor),
    ("pca",pca)
])

X_pca = pipeline_pca.fit_transform(X)

In [72]:
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
from sklearn.model_selection import GridSearchCV, KFold, cross_val_score

# Split the data into training and testing sets
from sklearn.model_selection import train_test_split
X_train_pca, X_test_pca, y_train_pca, y_test_pca = train_test_split(X_pca, y, test_size=0.2, random_state=42)

# Define the models
models = {
    'LinearRegression': LinearRegression(),
    'RandomForest': RandomForestRegressor(random_state=42),
    'XGBoost': XGBRegressor(random_state=42)
}

# Define the hyperparameter grids for each model
param_grids = {
    'LinearRegression': {},
    'RandomForest': {
        'n_estimators': [100, 200, 500],
        'max_depth': [None, 10, 30],
        'min_samples_split': [2, 5, 10],
    },
    'XGBoost': {
        'n_estimators': [100, 200, 500],
        'learning_rate': [0.01, 0.1, 0.3],
        'max_depth': [3, 6, 10],
    }
}

# 3-fold cross-validation
cv = KFold(n_splits=3, shuffle=True, random_state=42)

# Train and tune the models
grids_pca = {}
for model_name, model in models.items():
    #print(f'Training and tuning {model_name}...')
    grids_pca[model_name] = GridSearchCV(estimator=model, param_grid=param_grids[model_name], cv=cv, scoring='neg_mean_squared_error', n_jobs=-1, verbose=2)
    grids_pca[model_name].fit(X_train_pca, y_train_pca)
    best_params = grids_pca[model_name].best_params_
    best_score = np.sqrt(-1 * grids_pca[model_name].best_score_)
    
    print(f'Best parameters for {model_name}: {best_params}')
    print(f'Best RMSE for {model_name}: {best_score}\n')

Fitting 3 folds for each of 1 candidates, totalling 3 fits
[CV] END .................................................... total time=   0.0s
[CV] END .................................................... total time=   0.0s[CV] END .................................................... total time=   0.0s

Best parameters for LinearRegression: {}
Best RMSE for LinearRegression: 0.16344573463599196

Fitting 3 folds for each of 27 candidates, totalling 81 fits
[CV] END max_depth=None, min_samples_split=5, n_estimators=100; total time=   4.2s
[CV] END max_depth=None, min_samples_split=5, n_estimators=100; total time=   4.3s
[CV] END max_depth=None, min_samples_split=5, n_estimators=100; total time=   4.5s
[CV] END max_depth=None, min_samples_split=2, n_estimators=100; total time=   4.7s
[CV] END max_depth=None, min_samples_split=2, n_estimators=100; total time=   5.0s
[CV] END max_depth=None, min_samples_split=2, n_estimators=100; total time=   4.9s
[CV] END max_depth=None, min_samples_split=5,

In [73]:
from sklearn.neural_network import MLPRegressor

X_train_scaled_pca = X_train_pca.copy()
X_test_scaled_pca = X_test_pca.copy()

# Create an MLPRegressor instance
mlp = MLPRegressor(random_state=42,max_iter=10000, n_iter_no_change = 3,learning_rate_init=0.001)

# Define the parameter grid for tuning
param_grid = {
    'hidden_layer_sizes': [(10,), (10,10), (10,10,10), (25)],
    'activation': ['relu', 'tanh'],
    'solver': ['adam'],
    'alpha': [0.0001, 0.001, 0.01, .1, 1],
    'learning_rate': ['constant', 'invscaling', 'adaptive'],
}

# Create the GridSearchCV object
grid_search_mlp_pca = GridSearchCV(mlp, param_grid, scoring='neg_mean_squared_error', cv=3, n_jobs=-1, verbose=1)

# Fit the model on the training data
grid_search_mlp_pca.fit(X_train_scaled_pca, y_train)

# Print the best parameters found during the search
print("Best parameters found: ", grid_search_mlp_pca.best_params_)

# Evaluate the model on the test data
best_score = np.sqrt(-1 * grid_search_mlp_pca.best_score_)
print("Test score: ", best_score)

Fitting 3 folds for each of 120 candidates, totalling 360 fits
Best parameters found:  {'activation': 'tanh', 'alpha': 1, 'hidden_layer_sizes': (10, 10), 'learning_rate': 'constant', 'solver': 'adam'}
Test score:  0.21186122594798837


__NOTE__: 

Applyting the same fitting pipeline now, we achive _much_ better results with lienar regression, but slightly worse results with other methods. 

# Evaluating the model on _Test_ set

In [77]:
from sklearn.metrics import mean_squared_error
print("Without PCA")
for i in grids.keys():
    print (i + ': ' + str(np.sqrt(mean_squared_error(grids[i].predict(X_test), y_test))))

Without PCA
LinearRegression: 1902730217.9208043
RandomForest: 0.14746382556584564
XGBoost: 0.14400935453137015


In [79]:
from sklearn.metrics import mean_squared_error
print("With PCA")
for i in grids.keys():
    print (i + ': ' + str(np.sqrt(mean_squared_error(grids_pca[i].predict(X_test_pca), y_test))))

With PCA
LinearRegression: 0.1416261773725627
RandomForest: 0.1519648479685047
XGBoost: 0.1470669150792473


In [80]:
print("Without PCA MLP")
print( str(np.sqrt(mean_squared_error(grid_search_mlp.predict(X_test_scaled),y_test))))


Without PCA MLP
0.16456372948508957


In [82]:
print("With PCA MLP")
print( str(np.sqrt(mean_squared_error(grid_search_mlp_pca.predict(X_test_scaled_pca),y_test))))

With PCA MLP
0.16332837344493184


# Feature Engineering

Correcting features that are categorical to be numerical, etc


In [84]:
var_explore = df[['Fence','Alley','MiscFeature','PoolQC','FireplaceQu','GarageCond','GarageQual','GarageFinish','GarageType','BsmtExposure','BsmtFinType2','BsmtFinType1','BsmtCond','BsmtQual','MasVnrType','Electrical','MSZoning','Utilities','Exterior1st','Exterior2nd','KitchenQual','Functional','SaleType','LotFrontage','GarageYrBlt','MasVnrArea','BsmtFullBath','BsmtHalfBath','GarageCars','GarageArea','TotalBsmtSF']]

display_scrollable(var_explore)

In [85]:
from sklearn.preprocessing import FunctionTransformer

# feature engineering functions 
def custom_features(df):
    df_out = df.copy()
    df_out['PropertyAge'] = df_out['YrSold'] - df_out['YearBuilt']
    df_out['TotalSF'] = df_out['TotalBsmtSF'] + df_out['1stFlrSF'] + df_out['2ndFlrSF']
    df_out['TotalBath'] = df_out['FullBath'] + 0.5 * df_out['HalfBath'] + df_out['BsmtFullBath'] + 0.5 * df['BsmtHalfBath']
    df_out['HasRemodeled'] = (df_out['YearRemodAdd'] != df_out['YearBuilt']).astype(object)
    df_out['Has2ndFloor'] = (df_out['2ndFlrSF'] > 0).astype(object)
    df_out['HasGarage'] = (df_out['GarageArea'] > 0).astype(object)
    df_out['YrSold_cat'] = df_out['YrSold'].astype(object)
    df_out['MoSold_cat'] = df_out['MoSold'].astype(object)
    df_out['YearBuilt_cat'] = df_out['YearBuilt'].astype(object)
    df_out['MSSubClass_cat'] = df_out['MSSubClass'].astype(object)
    
    return df_out

feature_engineering_transformer = FunctionTransformer(custom_features)


In [86]:
# Identify categorical and numerical columns
new_cols_categorical = pd.Index(['HasRemodeled', 'Has2ndFloor', 'HasGarage'])
new_cols_numeric = pd.Index(['PropertyAge', 'TotalSF', 'TotalBath', 'YrSold_cat', 'MoSold_cat', 'YearBuilt_cat', 'MSSubClass_cat'])

# Update categorical and numerical columns
categorical_columns = df.select_dtypes(
    include=['object', 'category']).columns.append(new_cols_categorical)
numerical_columns = df.select_dtypes(
    include=['int64', 'float64']).columns.append(new_cols_numeric)

# Remove target variable from numerical columns
numerical_columns = numerical_columns.drop('SalePrice')

# Combine transformers using ColumnTransformer
preprocessor = ColumnTransformer(
    transformers=[
        ('num', numerical_transformer, numerical_columns),
        ('cat', categorical_transformer, categorical_columns)
    ],remainder = 'passthrough')

# Create a pipeline with the preprocessor
pipeline_fe = Pipeline(steps=[
    ('fe', feature_engineering_transformer),
    ('preprocessor', preprocessor),
    ('pca', pca)])

# Apply the pipeline to your dataset
X = df.drop('SalePrice', axis=1)
y = np.log(df['SalePrice'])
X_preprocessed_fe = pipeline_fe.fit_transform(X)

In [87]:
# Split the data into training and testing sets
from sklearn.model_selection import train_test_split
X_train_fe, X_test_fe, y_train_fe, y_test_fe = \
    train_test_split(X_preprocessed_fe, y, test_size=0.2, random_state=42)

# Define the models
models = {
    'LinearRegression': LinearRegression(),
    'RandomForest': RandomForestRegressor(random_state=42),
    'XGBoost': XGBRegressor(random_state=42)
}

# Define the hyperparameter grids for each model
param_grids = {
    'LinearRegression': {},
    'RandomForest': {
        'n_estimators': [100, 200, 500],
        'max_depth': [None, 10, 30],
        'min_samples_split': [2, 5, 10],
    },
    'XGBoost': {
        'n_estimators': [100, 200, 500],
        'learning_rate': [0.01, 0.1, 0.3],
        'max_depth': [3, 6, 10],
    }
}

# 3-fold cross-validation
cv = KFold(n_splits=3, shuffle=True, random_state=42)

# Train and tune the models
grids_fe = {}
for model_name, model in models.items():
    #print(f'Training and tuning {model_name}...')
    grids_fe[model_name] = GridSearchCV(estimator=model, param_grid=param_grids[model_name], cv=cv, scoring='neg_mean_squared_error', n_jobs=-1, verbose=2)
    grids_fe[model_name].fit(X_train_fe, y_train_fe)
    best_params = grids_fe[model_name].best_params_
    best_score = np.sqrt(-1 * grids_fe[model_name].best_score_)
    
    print(f'Best parameters for {model_name}: {best_params}')
    print(f'Best RMSE for {model_name}: {best_score}\n')

Fitting 3 folds for each of 1 candidates, totalling 3 fits
[CV] END .................................................... total time=   0.0s
[CV] END .................................................... total time=   0.1s
[CV] END .................................................... total time=   0.1s
Best parameters for LinearRegression: {}
Best RMSE for LinearRegression: 0.16384879744579967

Fitting 3 folds for each of 27 candidates, totalling 81 fits
[CV] END max_depth=None, min_samples_split=5, n_estimators=100; total time=   4.5s
[CV] END max_depth=None, min_samples_split=5, n_estimators=100; total time=   4.7s
[CV] END max_depth=None, min_samples_split=5, n_estimators=100; total time=   4.8s
[CV] END max_depth=None, min_samples_split=2, n_estimators=100; total time=   5.0s
[CV] END max_depth=None, min_samples_split=2, n_estimators=100; total time=   5.0s
[CV] END max_depth=None, min_samples_split=2, n_estimators=100; total time=   5.1s
[CV] END max_depth=None, min_samples_split=5,

In [88]:
X_train_scaled_fe = X_train_fe.copy()
X_test_scaled_fe = X_test_fe.copy()

# Create an MLPRegressor instance
from sklearn.neural_network import MLPRegressor

mlp = MLPRegressor(random_state=42, max_iter=10000, n_iter_no_change=3)

# Define the parameter grid for tuning
param_grid = {
    'hidden_layer_sizes': [(10,), (10, 10), (10, 25)],
    'activation': ['relu', 'tanh', 'sigmoid'],
    'solver': ['adam', 'sgd'],
    'alpha': [.1, .5, 1, 10, 100],
    'learning_rate': ['constant', 'invscaling', 'adaptive'],
    'learning_rate_init' : [0.1]
}

# Create the GridSearchCV object
from sklearn.model_selection import GridSearchCV
grid_search_mlp_fe = GridSearchCV(mlp, param_grid, 
                                  scoring='neg_mean_squared_error', 
                                  cv=3, n_jobs=-1, verbose=0)

# Fit the model on the training data
grid_search_mlp_fe.fit(X_train_scaled_fe, y_train_fe)

# Print the best parameters found during the search
print("Best parameters found: ", grid_search_mlp_fe.best_params_)

# Evaluate the model on the test data
best_score = np.sqrt(-1 * grid_search_mlp_fe.best_score_)
print("Test score: ", best_score)

/home/vsevolod/anaconda3/envs/PyBlastAfterglow/lib/python3.9/site-packages/sklearn/utils/extmath.py:153: RuntimeWarning: overflow encountered in matmul
  ret = a @ b
/home/vsevolod/anaconda3/envs/PyBlastAfterglow/lib/python3.9/site-packages/sklearn/neural_network/_base.py:174: RuntimeWarning: overflow encountered in square
  return ((y_true - y_pred) ** 2).mean() / 2
/home/vsevolod/anaconda3/envs/PyBlastAfterglow/lib/python3.9/site-packages/sklearn/utils/extmath.py:153: RuntimeWarning: invalid value encountered in matmul
  ret = a @ b
/home/vsevolod/anaconda3/envs/PyBlastAfterglow/lib/python3.9/site-packages/sklearn/utils/extmath.py:153: RuntimeWarning: overflow encountered in matmul
  ret = a @ b
/home/vsevolod/anaconda3/envs/PyBlastAfterglow/lib/python3.9/site-packages/sklearn/utils/extmath.py:153: RuntimeWarning: invalid value encountered in matmul
  ret = a @ b
/home/vsevolod/anaconda3/envs/PyBlastAfterglow/lib/python3.9/site-packages/sklearn/neural_network/_base.py:174: RuntimeWar

Best parameters found:  {'activation': 'tanh', 'alpha': 0.5, 'hidden_layer_sizes': (10, 10), 'learning_rate': 'adaptive', 'learning_rate_init': 0.1, 'solver': 'sgd'}
Test score:  0.12952493365335696


# Exploring Ensemble Learning


In [ ]:
from sklearn.ensemble import StackingRegressor

grids_fe['MLP'] =   grid_search_mlp_fe

best_estimators = [(model_name, grid.best_estimator_) for model_name, grid in grids_fe.items()]

# Define the candidate meta-models
meta_models = {
    'MLP': MLPRegressor(random_state=42, max_iter=10000, n_iter_no_change=3, learning_rate_init=0.001),
    'LinearRegression': LinearRegression(),
    'XGBoost': XGBRegressor(random_state=42)
}

# Define the hyperparameter grids for each meta-model
meta_param_grids = {
    'MLP': {
        'final_estimator__hidden_layer_sizes': [(10,), (10, 10)],
        'final_estimator__activation': ['relu', 'tanh'],
        'final_estimator__solver': ['adam', 'sgd'],
        'final_estimator__alpha': [ 0.001, 0.01, .1, .5],
        'final_estimator__learning_rate': ['constant', 'invscaling', 'adaptive'],
    },
    'LinearRegression': {},
    'XGBoost': {
        'final_estimator__n_estimators': [100, 200, 500],
        'final_estimator__learning_rate': [0.01, 0.1, 0.3],
        'final_estimator__max_depth': [3, 6, 10],
    }
}

# 3-fold cross-validation
cv = KFold(n_splits=3, shuffle=True, random_state=42)

# Train and tune the stacking ensemble
best_score = float('inf')
best_model = None

for meta_name, meta_model in meta_models.items():
    print(f'Training and tuning {meta_name} as the meta-model...')
    stacking_regressor = StackingRegressor(estimators=best_estimators, final_estimator=meta_model, cv=cv)
    grid_search = GridSearchCV(estimator=stacking_regressor, param_grid=meta_param_grids[meta_name], cv=cv, scoring='neg_mean_squared_error', n_jobs=-1, verbose=1)
    grid_search.fit(X_train_fe, y_train_fe)
    best_params = grid_search.best_params_
    best_rmse = np.sqrt(-1 * grid_search.best_score_)
    
    print(f'Best parameters for {meta_name}: {best_params}')
    print(f'Best RMSE for {meta_name}: {best_rmse}\n')
    
    if best_rmse < best_score:
        best_score = best_rmse
        best_model = grid_search

# Evaluate the best stacking ensemble on the test data
y_pred = best_model.predict(X_test_fe)
rmse = np.sqrt(mean_squared_error(y_test_fe, y_pred))
print(f"Best stacking ensemble's RMSE on test data: {rmse}")